In [1]:
import numpy as np
import matplotlib.pyplot as plt
import os
from PIL import Image
import cv2
import torch
import torch.nn as nn
import pandas as pd
import re
import librosa
import csv
import shutil
from sklearn.preprocessing import LabelEncoder

In [2]:
root = '../dataset_2020/'

In [3]:
#user_list = os.listdir(root)
user_list = ['user01', 'user02', 'user03', 'user04']
print(user_list)

['user01', 'user02', 'user03', 'user04']


In [13]:
def acc_mfcc(X, Y, Z):
    X = np.array(X)
    Y = np.array(Y)
    Z = np.array(Z)


    sr = 16000
    D_x = np.abs(librosa.stft(X, n_fft = 2048, win_length = 2048, hop_length = 512))
    mfcc_x = librosa.feature.mfcc(S = librosa.power_to_db(D_x), sr = sr, n_mfcc = 20)
    D_y = np.abs(librosa.stft(Y, n_fft = 2048, win_length = 2048, hop_length = 512))
    mfcc_y = librosa.feature.mfcc(S = librosa.power_to_db(D_y), sr = sr, n_mfcc = 20)
    D_z = np.abs(librosa.stft(Z, n_fft = 2048, win_length = 2048, hop_length = 512))
    mfcc_z = librosa.feature.mfcc(S = librosa.power_to_db(D_z), sr = sr, n_mfcc = 20)
    mfcc = np.stack((mfcc_x, mfcc_y, mfcc_z), axis=2)
    return mfcc

In [14]:
if os.path.exists('mfcc_data_3channel.csv'):
    os.remove('mfcc_data_3channel.csv')
    f = open('mfcc_data_3channel.csv','w', newline='')
    wr = csv.writer(f)
else:
    f = open('mfcc_data_3channel.csv','w', newline='')
    wr = csv.writer(f)

In [15]:
label_set = [ 82, 322, 793, 213, 713, 81, 121, 212, 211, 314, 131, 43, 725, 122, 722, 724, 133, 91,
 723, 313, 762, 711, 721, 61, 112, 111, 42, 92, 751, 132, 84, 311, 764, 41, 86, 743,
 763, 46, 134, 742, 85, 791, 712, 756, 87, 754, 752]
label_set.sort()
encoder = LabelEncoder()
encoder.fit(label_set)
action_label = encoder.transform(label_set)
print(action_label)

action_dict = {key: value for key, value in zip(label_set, action_label)}
print(action_dict)

[ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19 20 21 22 23
 24 25 26 27 28 29 30 31 32 33 34 35 36 37 38 39 40 41 42 43 44 45 46]
{41: 0, 42: 1, 43: 2, 46: 3, 61: 4, 81: 5, 82: 6, 84: 7, 85: 8, 86: 9, 87: 10, 91: 11, 92: 12, 111: 13, 112: 14, 121: 15, 122: 16, 131: 17, 132: 18, 133: 19, 134: 20, 211: 21, 212: 22, 213: 23, 311: 24, 313: 25, 314: 26, 322: 27, 711: 28, 712: 29, 713: 30, 721: 31, 722: 32, 723: 33, 724: 34, 725: 35, 742: 36, 743: 37, 751: 38, 752: 39, 754: 40, 756: 41, 762: 42, 763: 43, 764: 44, 791: 45, 793: 46}


In [16]:
for user in user_list:
    path = os.path.join(root, str(user))
    data_list = os.listdir(path)
    for data in data_list:
        data_path = os.path.join(path, str(data))
        if not os.path.exists(data_path + '/mfcc/'):
            os.mkdir(data_path + '/mfcc/')
        else:
            shutil.rmtree(data_path + '/mfcc/')
            os.mkdir(data_path + '/mfcc/')
        label_name = os.path.join(data_path, data + '_label.csv')
        df = pd.read_csv(label_name)
        element = list(map(int, list(df['ts'])))
        #print(element)
        for e in element:
            e4_path = os.path.join(data_path, 'e4Acc', str(e) + '.csv')
            if not os.path.isfile(e4_path):
                idx = df[df['ts']==e].index
                df = df.drop(idx)
                continue
            df2 = pd.read_csv(e4_path)
            X = list(df2['x'])
            Y = list(df2['y'])
            Z = list(df2['z'])
            mfcc_feature = acc_mfcc(X, Y, Z)
            fn = os.path.join(data_path, 'mfcc', str(e) + '.jpeg')
            label = df[df['ts']==e]['actionOption'].values[0]
            en_label = action_dict[label]
            label_set.append(label)
            #print(label)
            if mfcc_feature.shape != (20, 4):
                #img = Image.fromarray(mfcc_feature)
                img = cv2.resize(mfcc_feature, (4, 20))
                #mfcc_feature = np.asarray(img)
                # print(mfcc_feature.shape)
            # print(mfcc_feature.shape)
            cv2.imwrite(fn, mfcc_feature)
            wr.writerow([fn, label, en_label])
        #l = list(df['actionOption'])
        #label.extend(l)

f.close()
#print(len(label))
#print(len(mfcc_feature))

/home/jh/anaconda3/envs/pytorch_env/lib/python3.9/site-packages/librosa/core/spectrum.py:256: UserWarning: n_fft=2048 is too large for input signal of length=1920
  warnings.warn(
/home/jh/anaconda3/envs/pytorch_env/lib/python3.9/site-packages/librosa/core/spectrum.py:256: UserWarning: n_fft=2048 is too large for input signal of length=1920
  warnings.warn(
/home/jh/anaconda3/envs/pytorch_env/lib/python3.9/site-packages/librosa/core/spectrum.py:256: UserWarning: n_fft=2048 is too large for input signal of length=1920
  warnings.warn(
/home/jh/anaconda3/envs/pytorch_env/lib/python3.9/site-packages/librosa/core/spectrum.py:256: UserWarning: n_fft=2048 is too large for input signal of length=1920
  warnings.warn(
/home/jh/anaconda3/envs/pytorch_env/lib/python3.9/site-packages/librosa/core/spectrum.py:256: UserWarning: n_fft=2048 is too large for input signal of length=1920
  warnings.warn(
/home/jh/anaconda3/envs/pytorch_env/lib/python3.9/site-packages/librosa/core/spectrum.py:256: UserWa